In [2]:

from sec_api import QueryApi



In [3]:
queryApi = QueryApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

query = {
  "query": { "query_string": { 
      "query": "formType:\"10-K\" AND entities.stateOfIncorporation: \"DE\" AND  filedAt:{2019-01-01 TO 2021-06-20}" 
    } },
  "from": "0",
  "size": "10",
  "sort": [{ "filedAt": { "order": "desc" } }]
}

filings = queryApi.get_filings(query)

print(filings)


Exception: API error: 429 - {"status":429,"error":"You send a lot of requests. We like that. But you exceeded the free query limit of 100 requests. Upgrade your account to get unlimited access. Visit sec-api.io for more."}

In [ ]:
type(filings)

In [ ]:
# Where is the state that the company formed located?
# entities.stateOfIncorporation

In [ ]:
import pandas as pd
metadata = pd.DataFrame.from_records(filings["filings"])
metadata.head(5)


In [ ]:
metadata.info()

In [ ]:
pd.reset_option('display.max_colwidth')
metadata

In [ ]:
queryApi = QueryApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

query = {
  "query": { "query_string": { 
      "query": "formType:\"8-K\" AND entities.stateOfIncorporation: \"DE\" AND  filedAt:{2019-01-01 TO 2021-06-20}" 
    } },
  "from": "0",
  "size": "20",
  "sort": [{ "filedAt": { "order": "desc" } }]
}

filings8kDE = queryApi.get_filings(query)


In [ ]:
f8kDE = pd.DataFrame.from_records(filings8kDE["filings"])
f8kDE.head(5)

In [ ]:
f8kDE

In [ ]:
base_query = {
  "query": "PLACEHOLDER", # this will be set during runtime 
  "from": "0",
  "size": "200", # dont change this
  # sort by filedAt
  "sort": [{ "filedAt": { "order": "desc" } }]
}

In [ ]:
from sec_api import QueryApi

queryApi = QueryApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

In [ ]:
log_file = open("filing_urls.txt", "a")

# start with filings filed in 2021, then 2020, 2019, ... up to 2010 
# uncomment line below to fetch all filings filed in 2022-2010
for year in range(2024, 2000, -1):
#for year in range(2022, 2020, -1):
    print("starting {year}".format(year=year))
  
  # a single search universe is represented as a month of the given year
    for month in range(1, 13):
        # Construct the query for 10-Q and 10-Q/A filings filed in the given year and month
        universe_query = (
        "formType:\"10-K\" AND "
        "filedAt:[{year}-{month:02d}-01 TO {year}-{month:02d}-31] AND "
        "entities.stateOfIncorporation:\"DE\""
        ).format(year=year, month=month)
  
        print(universe_query)
    # set new query universe for year-month combination
        base_query["query"] = universe_query;

    # paginate through results by increasing "from" parameter 
    # until we don't find any matches anymore
    # uncomment line below to fetch 10,000 filings
    # for from_batch in range(0, 9800, 200): 
        for from_batch in range(0, 400, 200):
            # set new "from" starting position of search 
            base_query["from"] = from_batch;

            response = queryApi.get_filings(base_query)

      # no more filings in search universe
            if len(response["filings"]) == 0:
                break;

      # for each filing, only save the URL pointing to the filing itself 
      # and ignore all other data. 
      # the URL is set in the dict key "linkToFilingDetails"
        urls_list = list(map(lambda x: x["linkToFilingDetails"], response["filings"]))

      # transform list of URLs into one string by joining all list elements
      # and add a new-line character between each element.
        urls_string = "\n".join(urls_list) + "\n"
      
        log_file.write(urls_string)

log_file.close()

In [ ]:
import re

def search(text):
    lines = text.split('\n')
    
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    matches = []
       
    for lineNumber in range(len(lines)):
        context = lines[max(0, lineNumber-2):lineNumber+3]
        contextText = " ".join(context)
        
        if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
            matches.append((lineNumber + 1, lines[lineNumber]))
    
    return matches

filing_urls_file = "filing_urls.txt"

# Read each line of the text file
with open(filing_urls_file, 'r') as file:
    lines = file.readlines()

# Process each URL/path in the file
for line in lines:
    file_path = line.strip()  # Remove any leading/trailing whitespace or newline characters
    if not os.path.exists(file_path):
        print(f"File not found: {file_path}")
        continue

    with open(file_path, 'r', encoding='utf-8') as html_file:
        text = html_file.read()
        
    values = search(text)

    # Print the results for the current file
    print(f"Results for {file_path}:")
    for lineNumber, value in values:
        print(f"Line {lineNumber}: {value}")
    print("\n" + "-"*40 + "\n")  # Separator between results of different files


In [ ]:
#right code

In [4]:

import re
import os

def search(text):
    lines = text.split('\n')
    
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    matches = []
       
    for lineNumber in range(len(lines)):
        context = lines[max(0, lineNumber-2):lineNumber+3]
        contextText = " ".join(context)
        
        if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
            matches.append((lineNumber + 1, lines[lineNumber]))
    
    return matches

# test successful
#uncomment below lines for testing
file_path = "testCOW.txt"

with open(file_path, 'r', encoding='utf-8') as file:
    text = file.read()

values = search(text)

# Print the results for the current file
print(f"Results for {file_path}:")
for lineNumber, value in values:
    print(f"Line {lineNumber}: {value}")


Results for testCOW.txt:
Line 5: cvdgjb
Line 6: dgdsvhb
Line 7: The corporate opportunity waiver was included in the company's bylaws.
Line 8: Another section discusses business opportunities that directors might disclaim.
Line 9: It is important to renounce any potential conflicts in commercial opportunities.
Line 10: wwwww
Line 11: www
Line 14: f
Line 15: dgddgd
Line 16: The company's policy is to waive certain commercial opportunities.
Line 17: sdgdv
Line 18: fgf


In [ ]:
# What do we want
# we want to download 10-k's from Delaware and store locally in a folder

#problem rn
# test is working 
# only able to get the .htm files of the 10Ks
# NOT ABLE TO DOWNLOAD THEM AND PUT INTO A TXT FILE


In [ ]:
#Attempt 1

In [ ]:
#Not able to open and donwload
# 403 error
#BUT I HAVE API access


import os
import requests

def download_and_save(url, dest_folder):
    if not os.path.exists(dest_folder):
        os.makedirs(dest_folder)
    
    filename = os.path.join(dest_folder, url.split("/")[-1].replace('.htm', '.txt'))
    
    try:
        response = requests.get(url)
        response.raise_for_status()  # Check if the request was successful
        with open(filename, 'w', encoding='utf-8') as f:
            f.write(response.text)
        print(f"Downloaded and saved {url} to {filename}")
    except requests.exceptions.RequestException as e:
        print(f"Failed to retrieve {url}: {e}")

filing_urls_file = "filing_urls.txt"
dest_folder = "C:\\Users\\sidha\\OneDrive\\Sid\\MSF\\Summer\\RA\\Code\\10-K"

# Read each line of the text file
with open(filing_urls_file, 'r') as file:
    urls = file.readlines()

# Process each URL in the file
for url in urls:
    url = url.strip()  # Remove any leading/trailing whitespace or newline characters
    download_and_save(url, dest_folder)


In [ ]:
#Attempt 2
#Reference: https://medium.com/@jan_5421/how-to-download-and-scrape-10-k-filings-from-sec-edgar-b0d245fc8d48


In [ ]:
from sec_api import QueryApi

queryApi = QueryApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

In [ ]:

log_file = open("filing_urls.txt", "a")

for year in range(2022, 2020, -1):
    print("Starting download for year {year}".format(year=year))
  
  # a single search universe is represented as a month of the given year
    for month in range(1, 13, 1):
    # get 10-Q and 10-Q/A filings filed in year and month
    # resulting query example: "formType:\"10-Q\" AND filedAt:[2021-01-01 TO 2021-01-31]"
        universe_query = \
        "formType:(\"10-K\", \"10-KT\", \"10KSB\", \"10KT405\", \"10KSB40\", \"10-K405\") AND " + \
        "filedAt:[{year}-{month:02d}-01 TO {year}-{month:02d}-31]" \
        .format(year=year, month=month)
  
    # set new query universe for year-month combination
        base_query["query"]["query_string"]["query"] = universe_query;

    # paginate through results by increasing "from" parameter 
    # until we don't find any matches anymore
    # uncomment next line to fetch all 10,000 filings
    # for from_batch in range(0, 9800, 200): 
        for from_batch in range(0, 400, 200):
                      
      # set new "from" starting position of search 
            base_query["from"] = from_batch;

            response = queryApi.get_filings(base_query)

      # no more filings in search universe
            if len(response["filings"]) == 0:
                break;

      # for each filing, only save the URL pointing to the filing itself 
      # and ignore all other data. 
      # the URL is set in the dict key "linkToFilingDetails"
            urls_list = list(map(lambda x: x["linkToFilingDetails"], response["filings"]))

      # transform list of URLs into one string by joining all list elements
      # and add a new-line character between each element.
            urls_string = "\n".join(urls_list) + "\n"
      
            log_file.write(urls_string)

    print("Filing URLs downloaded for {year}-{month:02d}".format(year=year, month=month))

log_file.close()

print("All URLs downloaded")

In [ ]:
#Attempt 3
# Request quota exceeded 403
#Start downloading all filings
#39 filing URLs loaded
#Problem with https://www.sec.gov/Archives/edgar/data/1985554/000168316824000248/londax_i10q-113023.htm
#API error: 429 - Request quota exceeded
#Problem with https://www.sec.gov/Archives/edgar/data/1333822/000095017024004103/leds-20231130.htm


In [ ]:
#Attempt 4 --> <Most successful

In [ ]:
from sec_api import RenderApi

renderApi = RenderApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

In [25]:
#Code works
#Request 200

#Creating 1 file locally

import requests

# Assuming `text` contains the URL from which you need to extract the first 90 characters
firstURL = text[0:90]

# Define the User-Agent header
headers = {
    'User-Agent': 'MyEDGARScript/1.0 (varghesb@bc.edu)' # Replace with your app name and contact email
}

# Make the request with the headers
r = requests.get(firstURL, headers=headers)

file_path = r"C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test.txt"
with open(file_path, 'w', encoding='utf-8') as file:
        file.write(r.text)

# Check the response



In [33]:
#Printing contents of 1 file

path = r"C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test.txt"
with open(path, 'r', encoding='utf-8') as file:
    text = file.read()
    
values = search(text)

print(f"Results for {file_path}:")
for lineNumber, value in values:
    print(f"Line {lineNumber}: {value}") 


Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test.txt:
Line 3843:     <div style="break-before: page; margin-top: 6pt; margin-bottom: 6pt"><p style="margin: 0pt">&#160;</p></div>
Line 3844:     <!-- Field: /Page -->
Line 3845: The corporate opportunity waiver was included in the company's bylaws.
Line 3846: <p style="font: 10pt Times New Roman, Times, Serif; margin: 0pt 0; text-align: justify">&#160;</p>
Line 3847: 


In [ ]:





file_path = 

with open(file_path, 'r', encoding='utf-8') as file:
    text = file.read()

values = search(text)

# Print the results for the current file
print(f"Results for {file_path}:")
for lineNumber, value in values:
    print(f"Line {lineNumber}: {value}")

In [38]:
#Printing contents of 10 files
file_path = "filing_urls.txt"

with open(file_path, 'r', encoding='utf-8') as file:
    urlLinks = file.read()
urlLinks

'https://www.sec.gov/Archives/edgar/data/1829311/000168316824000250/bitmine_i10q-113023.htm\nhttps://www.sec.gov/Archives/edgar/data/1985554/000168316824000248/londax_i10q-113023.htm\nhttps://www.sec.gov/Archives/edgar/data/1333822/000095017024004103/leds-20231130.htm\nhttps://www.sec.gov/Archives/edgar/data/1584480/000164033424000046/laab_10q.htm\nhttps://www.sec.gov/Archives/edgar/data/1468978/000147793224000134/sitsf_10q.htm\nhttps://www.sec.gov/Archives/edgar/data/98338/000121390024003017/f10q1123_tsrinc.htm\nhttps://www.sec.gov/Archives/edgar/data/31667/000118518524000066/edc20231130_10q.htm\nhttps://www.sec.gov/Archives/edgar/data/1570132/000107997324000058/anvi_10q.htm\nhttps://www.sec.gov/Archives/edgar/data/1552033/000155203324000009/tru-20230930.htm\nhttps://www.sec.gov/Archives/edgar/data/1138724/000175612524000022/form10q.htm\nhttps://www.sec.gov/Archives/edgar/data/1522222/000118518524000064/cls20231130_10q.htm\nhttps://www.sec.gov/Archives/edgar/data/1603793/0001493152240

In [39]:
#Code works!
# Creating 10 files locally
urls = urlLinks.split('\n')
headers = {
    'User-Agent': 'MyEDGARScript/1.0 (varghesb@bc.edu)'  # Replace with your email
}

# Process the first ten URLs
for i in range(10):
    # Extract the URL
    url = urls[i]
    
    # Make the request with the headers
    r = requests.get(url, headers=headers)
    
    # Define the file path for each file
    file_path = f"C:\\Users\\sidha\\OneDrive\\Sid\\MSF\\Summer\\RA\\Code\\10-Q\\test{i+1}.txt"
    
    # Save the response text to the file
    with open(file_path, 'w', encoding='utf-8') as file:
        file.write(r.text)
    
    print(f"Response saved to {file_path}")
    
    # Wait for a few seconds before making another request (adjust the number of seconds as per the rate limit)
    time.sleep(0.2)

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test1.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test2.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test3.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test4.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test5.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test6.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test7.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test8.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test9.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-Q\test10.txt


In [14]:
import requests
import time

# API key and base URL
api_key = 'fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc'  # Replace with your actual API key
base_url = 'https://api.sec-api.io'

# Define the headers with the Authorization key
headers = {
    'Authorization': api_key,
    'Content-Type': 'application/json',
    'User-Agent': 'MyEDGARScript/1.0 (varghesb@bc.edu)'  # Replace with your email
}

# Define a function to make the POST request
def get_filings(query, from_batch):
    payload = {
        "query": query,
        "from": from_batch,
        "size": 200
    }
    response = requests.post(base_url, headers=headers, json=payload)
    
    try:
        response.raise_for_status()  # Check for request errors
        return response.json()
    except requests.exceptions.HTTPError as e:
        print(f"HTTPError: {e}")
        print(f"Status Code: {response.status_code}")
        print(f"Response Content: {response.content}")
        return None

# Open log file to write URLs
log_file = open("urlsDE.txt", "a")

# Start with filings filed in 2022
for year in range(2022, 2021, -1):
    print(f"Starting {year}")
  
    for month in range(1, 13):
        # Construct the query for 10-K filings filed in the given year and month
        universe_query = (
            f"formType:\"10-K\" AND "
            f"filedAt:[{year}-{month:02d}-01 TO {year}-{month:02d}-31] AND "
            f"entities.stateOfIncorporation:\"DE\""
        )
  
        print(universe_query)

        # Paginate through results
        for from_batch in range(0, 400, 200):
            response = get_filings(universe_query, from_batch)

            if response is None:
                # Skip to the next iteration if there was an error
                continue

            # Introduce a delay of 0.2 seconds between requests
            time.sleep(0.2)

            # No more filings in search universe
            if len(response["filings"]) == 0:
                break

      


Starting 2022
formType:"10-K" AND filedAt:[2022-01-01 TO 2022-01-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-02-01 TO 2022-02-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-03-01 TO 2022-03-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-04-01 TO 2022-04-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-05-01 TO 2022-05-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-06-01 TO 2022-06-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-07-01 TO 2022-07-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-08-01 TO 2022-08-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-09-01 TO 2022-09-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-10-01 TO 2022-10-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-11-01 TO 202

In [ ]:
#Delaware --> Code Works

In [44]:
queryApi = QueryApi(api_key="fccd7cd584373afdfd88b43603c9154b6e32f09659ca642276c6cb8e8a2d01dc")

query = {
  "query": { "query_string": { 
      "query": "formType:\"10-K\" AND entities.stateOfIncorporation: \"DE\" AND  filedAt:{2019-01-01 TO 2021-06-20}" 
    } },
  "from": "0",
  "size": "20",
  "sort": [{ "filedAt": { "order": "desc" } }]
}

filings10kDE = queryApi.get_filings(query)

In [48]:
print(filings10kDE)


{'total': {'value': 10000, 'relation': 'gte'}, 'query': {'from': 0, 'size': 20}, 'filings': [{'ticker': 'TEUM', 'formType': '10-K', 'accessionNo': '0001628280-21-012457', 'cik': '1084384', 'companyNameLong': 'PARETEUM Corp (Filer)', 'effectivenessDate': '2020-12-31', 'companyName': 'PARETEUM Corp', 'linkToFilingDetails': 'https://www.sec.gov/Archives/edgar/data/1084384/000162828021012457/teum-20201231.htm', 'description': 'Form 10-K - Annual report [Section 13 and 15(d), not S-K Item 405]', 'linkToTxt': 'https://www.sec.gov/Archives/edgar/data/1084384/000162828021012457/0001628280-21-012457.txt', 'filedAt': '2021-06-17T16:06:01-04:00', 'documentFormatFiles': [{'sequence': '1', 'size': '2947596', 'documentUrl': 'https://www.sec.gov/ix?doc=/Archives/edgar/data/1084384/000162828021012457/teum-20201231.htm', 'description': '10-K', 'type': '10-K'}, {'sequence': '2', 'size': '285525', 'documentUrl': 'https://www.sec.gov/Archives/edgar/data/1084384/000162828021012457/exhibit-31certificateofin

In [18]:
#Code Works
# 20 URLs copied onto 10kDE.txt



# Access the 'filings' key in the dictionary
filings = filings10kDE.get('filings', [])

# Open a file in write mode to store the URLs
with open('10kDE.txt', 'w') as file:
    # Iterate over each entry in the 'filings' list
    for entry in filings:
        # Get the value of the 'linkToTxt' key
        link_to_txt = entry.get('linkToTxt', '')
        # Write the URL to the file
        file.write(link_to_txt + '\n')


In [23]:
#Code works

#Step 1
#Base query

base_query = {
  "query": "PLACEHOLDER", # this will be set during runtime 
  "from": "0",
  "size": "200", # dont change this
  # sort by filedAt
  "sort": [{ "filedAt": { "order": "desc" } }]
}

In [24]:
#Code works

#Step 2: 
#Universal Query

#pastes 10kDE URLS onto 10kDE_extended.txt

# open the file we use to store the filing URLs
log_file = open("10kDE_extended.txt", "a")

# start with filings filed in 2021, then 2020, 2019, ... up to 2010 
# uncomment line below to fetch all filings filed in 2022-2010
# for year in range(2021, 2009, -1):
for year in range(2022, 2020, -1):
    print("starting {year}".format(year=year))
    
    # a single search universe is represented as a month of the given year
    for month in range(1, 13, 1):
        # get 10-Q and 10-Q/A filings filed in year and month
        # resulting query example: "formType:\"10-Q\" AND filedAt:[2021-01-01 TO 2021-01-31]"
        universe_query = (
            "formType:\"10-K\" AND "
            "filedAt:[{year}-{month:02d}-01 TO {year}-{month:02d}-31] AND "
            "entities.stateOfIncorporation:\"DE\""
        ).format(year=year, month=month)
        
        print(universe_query)
        # set new query universe for year-month combination
        base_query["query"] = universe_query;

        # paginate through results by increasing "from" parameter 
        # until we don't find any matches anymore
        # uncomment line below to fetch 10,000 filings
        # for from_batch in range(0, 9800, 200): 
        for from_batch in range(0, 400, 200):
            # set new "from" starting position of search 
            base_query["from"] = from_batch;

            response = queryApi.get_filings(base_query)

            # no more filings in search universe
            if len(response["filings"]) == 0:
                break;

            # for each filing, only save the URL pointing to the filing itself 
            # and ignore all other data. 
            # the URL is set in the dict key "linkToFilingDetails"
            urls_list = list(map(lambda x: x["linkToFilingDetails"], response["filings"]))

            # transform list of URLs into one string by joining all list elements
            # and add a new-line character between each element.
            urls_string = "\n".join(urls_list) + "\n"
            
            log_file.write(urls_string)

log_file.close()


starting 2022
formType:"10-K" AND filedAt:[2022-01-01 TO 2022-01-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-02-01 TO 2022-02-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-03-01 TO 2022-03-31] AND entities.stateOfIncorporation:"DE"
formType:"10-K" AND filedAt:[2022-04-01 TO 2022-04-31] AND entities.stateOfIncorporation:"DE"


KeyboardInterrupt: 

In [22]:

# let's inspect the content of file
log_file = open("10kDE_extended.txt", "r")
print(log_file.read()[0:2000])
log_file.close()

https://www.sec.gov/Archives/edgar/data/728447/000095017022000602/evoa-20201231.htm
https://www.sec.gov/Archives/edgar/data/1100397/000149315222002766/formnt10-k.htm
https://www.sec.gov/Archives/edgar/data/1816261/000119312522023409/d221966d10ka.htm
https://www.sec.gov/Archives/edgar/data/1869974/000149315222002707/form10-k.htm
https://www.sec.gov/Archives/edgar/data/1334325/000149315222002705/formnt10-k.htm
https://www.sec.gov/Archives/edgar/data/781902/000160706222000053/ibal063021formnt10k.htm
https://www.sec.gov/Archives/edgar/data/12927/000001292722000010/ba-20211231.htm
https://www.sec.gov/Archives/edgar/data/1814215/000110465922009084/twnd-20211231x10ka.htm
https://www.sec.gov/Archives/edgar/data/1801762/000149315222002559/formnt10-k.htm
https://www.sec.gov/Archives/edgar/data/1260221/000126022122000004/tdg-20210930.htm
https://www.sec.gov/Archives/edgar/data/920760/000162828022001450/len-20211130.htm
https://www.sec.gov/Archives/edgar/data/1084580/000108458022000006/jef-2021113

In [25]:
#Printing contents of 10 files
file_path = "10kDE_extended.txt"

with open(file_path, 'r', encoding='utf-8') as file:
    DE10kLinks = file.read()
DE10kLinks

'https://www.sec.gov/Archives/edgar/data/728447/000095017022000602/evoa-20201231.htm\nhttps://www.sec.gov/Archives/edgar/data/1100397/000149315222002766/formnt10-k.htm\nhttps://www.sec.gov/Archives/edgar/data/1816261/000119312522023409/d221966d10ka.htm\nhttps://www.sec.gov/Archives/edgar/data/1869974/000149315222002707/form10-k.htm\nhttps://www.sec.gov/Archives/edgar/data/1334325/000149315222002705/formnt10-k.htm\nhttps://www.sec.gov/Archives/edgar/data/781902/000160706222000053/ibal063021formnt10k.htm\nhttps://www.sec.gov/Archives/edgar/data/12927/000001292722000010/ba-20211231.htm\nhttps://www.sec.gov/Archives/edgar/data/1814215/000110465922009084/twnd-20211231x10ka.htm\nhttps://www.sec.gov/Archives/edgar/data/1801762/000149315222002559/formnt10-k.htm\nhttps://www.sec.gov/Archives/edgar/data/1260221/000126022122000004/tdg-20210930.htm\nhttps://www.sec.gov/Archives/edgar/data/920760/000162828022001450/len-20211130.htm\nhttps://www.sec.gov/Archives/edgar/data/1084580/000108458022000006

In [49]:
#Code works!
# Case 1: 10 file locally -- test
# Case 2: All files locally -- main

import re

cik_pattern = r'/data/(\d+)/'

headers = {
    'User-Agent': 'MyEDGARScript/1.0 (varghesb@bc.edu)'  # Replace with your email
}

# Case 1
#for i in range(10):
for url in DE10kLinks: 
   
    #url = DE10kLinks[i]                  # Case 1
    
    match = re.search(cik_pattern, url)
    if match:
        cik = match.group(1)
    else:
        cik = 'unknown'
    # Make the request with the headers
    r = requests.get(url, headers=headers)
    
    # Define the file path for each file
    file_path = f"C:\\Users\\sidha\\OneDrive\\Sid\\MSF\\Summer\\RA\\Code\\10-K\\DE\\{cik}.txt"
    # Save the response text to the file
    with open(file_path, 'w', encoding='utf-8') as file:
        file.write(r.text)
    
    print(f"Response saved to {file_path}")
    
    # Wait for a few seconds before making another request (adjust the number of seconds as per the rate limit)
    time.sleep(0.1)

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\728447.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1100397.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1816261.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1869974.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1334325.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\781902.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\12927.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1814215.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1801762.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1260221.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\920760.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1069530.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1650962.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1102112.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1512499.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\886163.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1806201.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1326141.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1072627.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1176948.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1083446.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1549922.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\1

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1029142.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\107263.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1488039.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1086222.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1792044.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1281895.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1759509.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1109242.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1129155.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1345016.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1327811.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\1

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1124804.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1025835.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1403256.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1058811.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1431695.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1651561.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\785161.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1437352.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1561550.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1367644.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1028918.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\1

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\52428.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\820027.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1048477.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\944148.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1651094.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1018963.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1040829.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1113232.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1086600.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1230245.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1842022.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K

...

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1832511.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1858503.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1845022.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1853651.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1652724.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\890821.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1835972.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1496671.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1823884.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1823882.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1814114.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\1

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1718405.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1661600.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1671858.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1865200.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1716166.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1790625.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1840161.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1449792.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1826671.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1622345.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1759824.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1573946.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1855351.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1585673.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1796160.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1448038.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1556811.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\883975.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\924719.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\830122.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1785592.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1872356.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-

Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1803914.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1837248.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1305773.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1447669.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1849294.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1780312.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\798081.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1823884.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\56868.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\320017.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1855168.txt
Response saved to C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K

ConnectionError: ('Connection aborted.', ConnectionResetError(10054, 'An existing connection was forcibly closed by the remote host', None, 10054, None))

In [45]:
len(DE10kLinks)

5062

In [46]:
len(DE10kLinksclean)

5062

In [1]:
####Libraries
import re
import requests
from sec_api import QueryApi


In [2]:
#### Text search function


import re
import os

def search(text):
    lines = text.split('\n')
    
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    matches = []
       
    for lineNumber in range(len(lines)):
        context = lines[max(0, lineNumber-2):lineNumber+3]
        contextText = " ".join(context)
        
        if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
            matches.append((lineNumber + 1, lines[lineNumber]))
    
    return matches

# test successful
#uncomment below lines for testing
#file_path = "testCOW.txt"

#with open(file_path, 'r', encoding='utf-8') as file:
 #   text = file.read()

#values = search(text)

# Print the results for the current file
#print(f"Results for {file_path}:")
#for lineNumber, value in values:
 #   print(f"Line {lineNumber}: {value}")


In [3]:
#### File search function

def searchFilesInDirectory(directory, limit=None):
    files = os.listdir(directory)
    if limit:
        files = files[:limit]
    
    for fileName in files:
        filePath = os.path.join(directory, fileName)
        if os.path.isfile(filePath):
            with open(filePath, 'r', encoding='utf-8') as file:
                text = file.read()
            
            values = search(text)

            # Print the results for the current file
            print(f"Results for {filePath}:")
            for lineNumber, value in values:
                print(f"Line {lineNumber}: {value}")

In [4]:
directoryPath = r"C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE"

# Case 1: Search the first 10 files
print("Searching the first 10 files:")
searchFilesInDirectory(directoryPath, limit=10)

# Case 2: Search all files
#print("\nSearching all files:")
#searchFilesInDirectory(directoryPath)

Searching the first 10 files:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1000683.txt:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1000694.txt:
Line 2: 
Line 3: 
Line 4: <title>nvax-20211231</title></head><body><div style="display:none"><ix:header><ix:hidden><ix:nonNumeric contextRef="ifd716755db974fdebb6ade1857ae9b7a_D20210101-20211231" name="dei:AmendmentFlag" format="ixt:fixed-false" id="id3VybDovL2RvY3MudjEvZG9jOjY1ZDA2MmNhMWQ3MDQ1YmU4ZTE1ZTc1YTI5MzEyYzJjL3NlYzo2NWQwNjJjYTFkNzA0NWJlOGUxNWU3NWEyOTMxMmMyY180L2ZyYWc6MjkwNGU2NjA2ZjE5NDU0YmJiMDNjZjI2NzFmNWJkNjEvdGFibGU6NTJlMmJlMmE3YjY4NDUzNTljM2MxYjdjNDk1NTY0ZjgvdGFibGVyYW5nZTo1MmUyYmUyYTdiNjg0NTM1OWMzYzFiN2M0OTU1NjRmOF80LTEtMS0xLTI4ODgz_6c47dc9e-3ae1-48b4-a092-817861b5d72b">FALSE</ix:nonNumeric><ix:nonNumeric contextRef="ifd716755db974fdebb6ade1857ae9b7a_D20210101-20211231" name="dei:DocumentFiscalYearFocus" id="id3VybDovL2RvY3MudjEvZG9jOjY1ZDA2MmNhMWQ3MDQ1YmU4ZTE1ZTc1YTI5MzEyYzJjL3NlYzo2NW

Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001171.txt:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001250.txt:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001601.txt:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001614.txt:
Line 2: 
Line 3: 
Line 4: <title>rep-20210930</title></head><body><div style="display:none"><ix:header><ix:hidden><ix:nonNumeric contextRef="i4662e2cbbb4c4c1d9b0894e0161fd5e1_D20201001-20210930" name="dei:EntityCentralIndexKey" id="id3VybDovL2RvY3MudjEvZG9jOjRiZTQ4ZmYzZmZkYzQzY2NhNmQ5NWE5OWEyMjljMmYwL3NlYzo0YmU0OGZmM2ZmZGM0M2NjYTZkOTVhOTlhMjI5YzJmMF8xMTk0L2ZyYWc6YTIyMGE2MGJiZWE0NDhhMGJiZDQ5Y2U5NWQ2Yzc4YWEvdGFibGU6NjAzYjYxNzk4YTE0NGY0Zjg1Y2Y2Njg0ODAzNjRhZjYvdGFibGVyYW5nZTo2MDNiNjE3OThhMTQ0ZjRmODVjZjY2ODQ4MDM2NGFmNl8wLTEtMS0xLTY0MzA2_3ab6f2db-c4d8-4166-baf9-84916edb057d">0001001614</ix:nonNumeric><ix:nonNumeric contextRef="i4662e2cbbb4c4c1d9b0894e0161fd5e1_D20201001-2021093

Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001838.txt:
Line 145: <div style="background-color:#000000;clear:both;height:2pt;page-break-after:always;width:79.3%;border:0;margin:30pt 10.35% 30pt 10.35%;"></div><div style="max-width:100%;padding-left:10.35%;padding-right:10.35%;position:relative;"><div style="margin-top:21.6pt;min-height:41.75pt;width:100%;"><p style="font-family:'Times New Roman','Times','serif';font-size:10pt;line-height:1.19;margin:0pt 0pt 30pt 0pt;"><a href="#TOC"><span style="font-family:'Times New Roman','Times','serif';font-size:10pt;font-style:normal;font-weight:normal;line-height:1.19;text-align:left;">Table of Contents</span></a></p><p style="font-family:'Times New Roman','Times','serif';font-size:10pt;line-height:1.19;text-align:center;margin:0pt;"><b style="font-weight:bold;">SOUTHERN COPPER CORPORATION AND SUBSIDIARIES</b></p><p style="font-family:'Times New Roman','Times','serif';font-size:10pt;line-height:1.19;text-align:center;marg

Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001907.txt:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1002135.txt:


In [9]:
#### Text Search Function 2.0

def search(text):
    # Split the text into words rather than lines
    words = re.split(r'\s+', text)
    
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    matches = []
    context = []
    withinSpan = False
    
    for word in words:
        # Check for <span> and </span> tags
        if '<span>' in word:
            withinSpan = True
            context.append(word.split('<span>')[1])  # Extract text after <span
        elif '</span>' in word:
            context.append(word.split('</span>')[0])  # Extract text before </span>
            withinSpan = False
        elif withinSpan:
            context.append(word)
        else:
            continue
        
        # Join context into a single string for pattern matching
        contextText = " ".join(context)
        
        if len(word) > 15:
            continue  # Skip over long strings which are likely XML code

        # If we found a match, store it
        if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
            matches.append(contextText)
            context = []  # Reset context after a match

    return matches


In [18]:
filePath = "testCOW2.txt"

with open(filePath, 'r', encoding='utf-8') as file:
    text = file.read()

values = search(text)

# Print the results for the current file
print(f"Results for {filePath}:")
for lineNumber, value in values:
    print(f"Line {lineNumber}: {value}")

Results for testCOW2.txt:


In [15]:
#### 3.0

def search(text):
    lines = text.split('\n')
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)

    matches = []
    context = []
    spanText = ""
    withinSpan = False

    for lineNumber, line in enumerate(lines):
        words = re.split(r'\s+', line)
        newContext = []

        for word in words:
            # Check for <span> and </span> tags
            if '<span>' in word :
                withinSpan = True
                spanText = word.split('<span>', 1)[1]  # Extract text after <span>
            elif '</span>' in word and withinSpan:
                spanText += " " + word.split('</span>', 1)[0]  # Extract text before </span>
                newContext.append(spanText)
                withinSpan = False
            elif withinSpan:
                spanText += " " + word
            else:
                continue

        if newContext:
            contextText = " ".join(newContext)

            # If we found a match, store it
            if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
                matches.append((lineNumber + 1, contextText))

    return matches

In [17]:
#### 4.0

import re
import os

def search(text):
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)

    matches = []
    context = []
    withinSpan = False
    spanText = ""
    lineNumber = 0

    for line in text:
        lineNumber += 1
        i = 0
        while i < len(line):
            # Start of a <span> tag
            if line[i:i+5] == "<span":
                withinSpan = True
                # Find the end of the <span> tag
                end_tag = line.find(">", i)
                if end_tag != -1:
                    i = end_tag + 1
            # End of a </span> tag
            elif line[i:i+7] == "</span>":
                if withinSpan:
                    withinSpan = False
                    newContext = spanText.strip()
                    context.append(newContext)
                    spanText = ""
                i += 7
            elif withinSpan:
                spanText += line[i]
                i += 1
            else:
                i += 1

        if context:
            contextText = " ".join(context)
            context = []
            # If we found a match, store it
            if (opportunityPattern.search(contextText) and actionPattern.search(contextText)) or fiduciaryPattern.search(contextText):
                matches.append((lineNumber, contextText))

    return matches

In [ ]:

# Things to take care of

# Text can be in same line or can be split across multiple lines
# The useful text is always between <span> and </span>. No spaces in between.
# <span> can have parameters like <span style = "Times New Roman">
# Output should be displayed as Line "line no, col no": "text"

In [23]:
# Code works


import re

def extractSpanText(text):
    lines = text.split('\n')
    
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    spanPattern = re.compile(r'<span.*?>', re.IGNORECASE)
    endSpanPattern = re.compile(r'</span>', re.IGNORECASE)

    withinSpan = False
    spanText = ""
    matches = []
    lineNumber = 0
    startColumn = 0

    for line in lines:
        lineNumber += 1
        i = 0
        while i < len(line):
            if not withinSpan:
                start = spanPattern.search(line, i)
                if start:
                    withinSpan = True
                    startColumn = start.start() + 1
                    i = start.end()
                else:
                    break
            else:
                end = endSpanPattern.search(line, i)
                if end:
                    spanText += line[i:end.start()]
                    matches.append((lineNumber, startColumn, spanText.strip()))
                    spanText = ""
                    withinSpan = False
                    i = end.end()
                else:
                    spanText += line[i:]
                    break
    return matches

# Specify the file path
filePath = "testSpan.txt"

# Read the contents of the file
with open(filePath, 'r', encoding='utf-8') as file:
    text = file.read()

# Extract text between span tags
values = extractSpanText(text)

# Print the results for the current file
print(f"Results for {filePath}:\n")
for lineNumber, startColumn, value in values:
    print(f"Line {lineNumber}, Column {startColumn}: {value}\n")


Results for testSpan.txt:

Line 14, Column 409: Ourbusiness has been materially and adversely affected by the outbreak of the Coronavirus or COVID-19. COVID-19, which has been declaredby the World Health Organization to be a &#8220;pandemic,&#8221; has spread to many countries, including the United States, and is impactingdomestic and worldwide economic activity. Since being declared a &#8220;pandemic&#8221;, COVID-19 interfered with our ability to meetwith certain customers during 2020 and continued into the first half of 2021. In addition, the COVID-19 outbreak has affected the supplychain for many types of products and materials, particularly those being manufactured in China and other countries where the outbreakhas resulted in significant disruptions to ongoing business activities. Beginning in the second quarter of 2021 and continuing into thefirst quarter of 2022, we experienced a material disruption in our supply chain as it relates to the procurement of certain sole sourceand 

In [49]:
import re

def search(text):
    lines = text.split('\n')
    
    # Patterns for searching
    opportunityPattern = re.compile(r'(corporate|commercial|business)\s+\S*opportun\w*', re.IGNORECASE)
    actionPattern = re.compile(r'(waiv\w*|renounc\w*|disclaim\w*)', re.IGNORECASE)
    #fiduciaryPattern = re.compile(r'fiduciary\s+(duty|loyalty)', re.IGNORECASE)
    
    spanPattern = re.compile(r'<span.*?>', re.IGNORECASE)
    endSpanPattern = re.compile(r'</span>', re.IGNORECASE)

    withinSpan = False
    spanText = ""
    matches = []
    lineNumber = 0
    startColumn = 0

    for line in lines:
        lineNumber += 1
        i = 0
        while i < len(line):
            if not withinSpan:
                start = spanPattern.search(line, i)
                if start:
                    withinSpan = True
                    startColumn = start.start() + 1
                    i = start.end()
                else:
                    break
            else:
                end = endSpanPattern.search(line, i)
                if end:
                    spanText += line[i:end.start()]
                    # Check if the span text matches any pattern
                    if (opportunityPattern.search(spanText) and actionPattern.search(spanText)): #or fiduciaryPattern.search(spanText):
                        matches.append((lineNumber, startColumn, spanText.strip()))
                        sentence = re.search(r'[^.]*\b(' + '|'.join(opportunityPattern.pattern.split('|') + actionPattern.pattern.split('|') #+ fiduciaryPattern.pattern.split('|'))
                                                                    + r')\b[^.]*\.', spanText))
                        if sentence:
                            matches.append((lineNumber, startColumn, sentence.group(0).strip()))
                    spanText = ""
                    withinSpan = False
                    i = end.end()
                else:
                    spanText += line[i:]
                    break
                    
    return matches

# Specify the file path
#filePath = "testCOW3.txt"
filePath = r"C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1000694.txt"

# Read the contents of the file
#with open(filePath, 'r', encoding='utf-8') as file:
  #  text = file.read()

# Extract text between span tags with conditions
#values = extract_span_text_with_conditions(text)

# Print the results for the current file
#print(f"Results for {filePath}:\n")
#for lineNumber, startColumn, value in values:
 #   print(f"Line {lineNumber}, Column {startColumn}: {value}\n")


In [50]:
#### File search function

def searchFilesInDirectory(directory, limit=None):
    files = os.listdir(directory)
    if limit:
        files = files[:limit]
    
    for fileName in files:
        filePath = os.path.join(directory, fileName)
        if os.path.isfile(filePath):
            with open(filePath, 'r', encoding='utf-8') as file:
                text = file.read()
            
            values = search(text)

            # Print the results for the current file
            print(f"Results for {filePath}:")
            print(values)
            #for lineNumber, value in values:
             #   print(f"Line {lineNumber}: {value}")

In [43]:
directoryPath = r"C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE"

# Case 1: Search the first 10 files
print("Searching the first 10 files:")
searchFilesInDirectory(directoryPath, limit=100)

# Case 2: Search all files
#print("\nSearching all files:")
#searchFilesInDirectory(directoryPath)

Searching the first 10 files:
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1000683.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1000694.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001171.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001250.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001601.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001614.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001838.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1001907.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1002135.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1002517.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Code\10-K\DE\1002590.txt:
[]
Results for C:\Users\sidha\OneDrive\Sid\MSF\Summer\RA\Cod